In [153]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import os
import sys
from statsmodels.graphics.tsaplots import plot_pacf,plot_acf
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import plotly.io as pio
pio.templates["mod"] = go.layout.Template(layout=dict(font=dict(family="Fira Code")))
pio.templates.default = "plotly_dark+mod"
%matplotlib inline

In [154]:
pd.set_option("display.float_format",'{:2f}'.format)

In [155]:
sys.path.append('./Downloads/store-sales-time-series-forecasting/')

In [156]:
if "google.colab" in sys.modules:
    train_sales = pd.read_csv('train.csv')
    stores = pd.read_csv('stores.csv')
    oil = pd.read_csv('oil.csv')
    sample_sub = pd.read_csv('sample_submission.csv')
    holidays = pd.read_csv('holidays_events.csv')
    test_sales = pd.read_csv('test.csv')
    transactions = pd.read_csv('transactions.csv')
else:
    train_sales = pd.read_csv('./store-sales-time-series-forecasting/train.csv')
    stores = pd.read_csv('./store-sales-time-series-forecasting/stores.csv')
    oil = pd.read_csv('./store-sales-time-series-forecasting/oil.csv')
    sample_sub = pd.read_csv('./store-sales-time-series-forecasting/sample_submission.csv')
    holidays = pd.read_csv('./store-sales-time-series-forecasting/holidays_events.csv')
    test_sales = pd.read_csv('./store-sales-time-series-forecasting/test.csv')
    transactions = pd.read_csv('./store-sales-time-series-forecasting/transactions.csv')

In [157]:
train_sales['date'] = pd.to_datetime(train_sales['date'])
test_sales['date'] = pd.to_datetime(test_sales['date'])
holidays['date'] = pd.to_datetime(holidays['date'])
oil['date'] = pd.to_datetime(oil['date'])

In [158]:
def change_index(data:pd.DataFrame):
    df = data.copy()
    df.set_index('date',inplace=True)
    return df

In [159]:
total = change_index(train_sales)
oil = change_index(oil)

In [160]:
total.head()

id  store_nbr      family    sales  onpromotion
date                                                       
2013-01-01   0          1  AUTOMOTIVE 0.000000            0
2013-01-01   1          1   BABY CARE 0.000000            0
2013-01-01   2          1      BEAUTY 0.000000            0
2013-01-01   3          1   BEVERAGES 0.000000            0
2013-01-01   4          1       BOOKS 0.000000            0

In [161]:
stores.head()

store_nbr           city                           state type  cluster
0          1          Quito                       Pichincha    D       13
1          2          Quito                       Pichincha    D       13
2          3          Quito                       Pichincha    D        8
3          4          Quito                       Pichincha    D        9
4          5  Santo Domingo  Santo Domingo de los Tsachilas    D        4

In [162]:
np.sort(stores['cluster'].unique())

array([ 1,  2,  3,  4,  5,  6,  7,  8,  9, 10, 11, 12, 13, 14, 15, 16, 17])

In [163]:
time_steps = train_sales.date.nunique()
total_series = train_sales.family.nunique() * train_sales.store_nbr.nunique()

In [164]:
# total_arr = np.zeros(shape=(1782,1684))
# i = 0
# for s in np.sort(total.store_nbr.unique()):
#     for f in total.family.unique():
#         total_arr[i,:] = total.loc[(total['family'] == f) & (total['store_nbr'] == s),'sales']
#         i += 1
# def generate_series(batch_size,n_steps):
#     offset1,offset2,freq1,freq2 = np.random.rand(4,batch_size,1)
#     time_steps = np.linspace(0,1,n_steps)
#     ser = 0.5 * np.sin((time_steps-offset1)*(freq1*10+10))
#     ser += 0.2 * np.sin((time_steps-offset2)*(freq2*20+20))
#     ser += 0.1 * (np.random.randn(batch_size,n_steps)-0.5)
#     return ser[...,np.newaxis].astype(np.float32)
# n_steps = 50
# seri = generate_series(10000,n_steps+10)
# X_train_steps = seri[:7000,:n_steps]
# X_valid_steps = seri[7000:9000,:n_steps]
# X_test_steps = seri[9000:,:n_steps]
# Y = np.empty((10000,n_steps,10))
# for step_ahead in range(1,10+1):
#     Y[:,:,step_ahead-1] = seri[:,step_ahead:step_ahead+n_steps,0]
# Y_train_steps = Y[:7000]
# Y_valid_steps = Y[7000:9000]
# Y_test_steps = Y[9000:]

In [165]:
total.head()

id  store_nbr      family    sales  onpromotion
date                                                       
2013-01-01   0          1  AUTOMOTIVE 0.000000            0
2013-01-01   1          1   BABY CARE 0.000000            0
2013-01-01   2          1      BEAUTY 0.000000            0
2013-01-01   3          1   BEVERAGES 0.000000            0
2013-01-01   4          1       BOOKS 0.000000            0

In [166]:
train = train_sales.copy()
train['date'] = pd.to_datetime(train['date'])

In [167]:
summ = train.groupby(['store_nbr','family','date']).sum().copy()
summ.head()

id    sales  onpromotion
store_nbr family     date                                  
1         AUTOMOTIVE 2013-01-01     0 0.000000            0
                     2013-01-02  1782 2.000000            0
                     2013-01-03  3564 3.000000            0
                     2013-01-04  5346 3.000000            0
                     2013-01-05  7128 5.000000            0

In [168]:
def plot_series(cols:str or list,store_num:int):
    fig = go.Figure()
    global ind
    ind = summ.loc[(1,'AUTOMOTIVE')].index
    all_cols = summ.loc[1].index.to_frame()['family'].unique()
    if cols == 'all' and isinstance(cols,str):
        fig.add_trace(go.Scatter(y=summ.loc[(store_num,all_cols[0]),'sales'],mode="lines",name=all_cols[0]))
        for col in all_cols[1:]:
            fig.add_trace(go.Scatter(y=summ.loc[(store_num,col),'sales'],mode="lines",name=col,visible='legendonly'))
    else:
        fig.add_trace(go.Scatter(y=summ.loc[(store_num,cols[0]),'sales'],mode="lines",name=cols[0]))
        for col in cols[1:]:
            fig.add_trace(go.Scatter(x=ind,y=summ.loc[(store_num,col),'sales'],mode="lines",name=col,visible='lengendonly'))
    fig.update_traces(x=ind)
    fig.add_vline(x='2016-04-16',opacity=0.2,line=dict(dash="dash"))
    # fig.update_xaxes(overwrite=False,tickmode="array",tickvals=['2016-04-16'],ticktext=["Earthquake"])
    # fig.update_xaxes(labelalias={"April 4,2016":"EarthQuake"})
    # fig.add_annotation(x="2016-04-16",y=1,text="Earthquake",showarrow=False,font=dict(size=20,color="red"),valign='top',yref='paper')
    fig.add_annotation(x='2016-04-16',y=0,text="EarthQuake",showarrow=False,xref='x',yref='paper',yanchor='top',font=dict(size=15,color="red"),textangle=90)
    fig.update_layout(hovermode=False)
    fig.show()

In [169]:
plot_series('all',store_num=1)

In [170]:
def plot_rolling(cols:'all' or list,store_num:int):
    fig = make_subplots(rows=2,cols=1,shared_xaxes=True,subplot_titles=['All Stores with their Families','Oil Prices'],row_heights=[0.7,0.3],vertical_spacing=0.05)
    all_cols = summ.loc[1].index.to_frame()['family'].unique()
    if cols == 'all' and isinstance(cols,str):
        fig.add_trace(go.Scatter(y=summ.loc[(store_num,all_cols[0]),'sales'].rolling(60,min_periods=15,center=True).mean(),mode="lines",name=all_cols[0]),row=1,col=1)
        for col in all_cols[1:]:
            fig.add_trace(go.Scatter(y=summ.loc[(store_num,col),'sales'].rolling(60,min_periods=15,center=True).mean(),mode="lines",name=col,visible='legendonly'),row=1,col=1)
    else:
        fig.add_trace(go.Scatter(y=summ.loc[(store_num,cols[0]),'sales'].rolling(60,min_periods=15,center=True).mean(),mode="lines",name=cols[0]),row=1,col=1)
        for col in cols[1:]:
            fig.add_trace(go.Scatter(x=ind,y=summ.loc[(store_num,col),'sales'].rolling(60,min_periods=15,center=True).mean(),mode="lines",name=col,visible='lengendonly'),row=1,col=1)
    fig.add_trace(go.Scatter(x=oil.index,y=oil.dcoilwtico,mode="lines",name="Oil Prices"),row=2,col=1)
    fig.update_traces(x=ind,row=1,col=1)
    fig.add_vline(x='2016-04-16',opacity=0.2,line=dict(dash="dash"))
    # fig.update_xaxes(overwrite=False,tickmode="array",tickvals=['2016-04-16'],ticktext=["Earthquake"])
    # fig.update_xaxes(labelalias={"April 4,2016":"EarthQuake"})
    # fig.add_annotation(x="2016-04-16",y=1,text="Earthquake",showarrow=False,font=dict(size=20,color="red"),valign='top',yref='paper')
    fig.add_annotation(x='2016-04-16',y=0,text="EarthQuake",showarrow=False,xref='x',yref='paper',yanchor='top',font=dict(size=12,color="red"),textangle=90,borderwidth=1)
    fig.update_layout(hovermode=False,height=800)
    fig.show()

In [171]:
plot_rolling('all',1)

### Earthquake effected some families 

In [172]:
def gen_series(batch_size,n_steps):
    off1,off2,freq1,freq2 = np.random.rand(4,batch_size,1)
    time = np.linspace(0,1,n_steps)
    series = 0.5 * np.sin((time-off1)*(freq1*10+10))
    series += 0.2 * np.sin((time-off2)*(freq2*20+20))
    series += 0.1 * np.random.randn(batch_size,n_steps)
    return series[...,np.newaxis]

In [173]:
holidays.transferred.value_counts()

False    338
True      12
Name: transferred, dtype: int64

In [174]:
# def plot_holidays(store_num:int,local:str):
#     fig = go.Figure()
#     fig.add_trace(go.Scatter(y=summ.loc[(store_num,'AUTOMOTIVE'),'sales'],mode="lines",name="AUTOMOTIVE"))
#     for col in train_sales.family.unique()[1:]:
#         fig.add_trace(go.Scatter(y=summ.loc[(store_num,col),'sales'],mode="lines",visible='legendonly',name=f"{col}"))
#     for h_day in holidays.query(f"locale == '{local}'").index:
#         fig.add_vline(x=h_day,line=dict(dash='dash',color='rgba(255,0,0,0.5)'))
#     fig.update_traces(x=ind)
#     fig.update_layout(hovermode=False)
#     fig.show()

In [175]:
fig = make_subplots(rows=2,cols=1,row_heights=[0.6,0.4],vertical_spacing=0.05,shared_xaxes=True)
fig.add_trace(go.Scatter(x=oil.index,y=oil[oil.columns[0]].to_numpy(),mode="lines",name="Oil"),row=2,col=1)
fig.add_trace(go.Scatter(x=ind,y=train_sales.groupby(['date']).sum()['sales'].rolling(60,min_periods=15,center=True).mean(),mode="lines",name="Sales"),row=1,col=1)
fig.update_layout(height=700)
fig.show()

### Oil Prices are roughly inversely proportional to total sales for every timestep

<font face = "Firacode">
<font size = 10>
Strategy <br>
</font>
<font face = "Firacode">
<font size = 5>
<ol>
<li>Fill the oil column with proper values and merge with total</li>
<li>Tackle the holidays column</li>
<ul>
    <li>Make 3 columns Weekday,Weekend,Holidays</li>
    <li>Weekday and Weekend are opposite and Holidays is a seperate column</li>
    <li>Make the holidays appropriate by filling the places where it is actually celebrated</li>
</ul>
<li>Merge cluster and get dummies to the total</li>
<li>Group the total with ['store_nbr','family','date'] then reshape the dataframe and get the series</li>
</ol>
The End
</font>

<font face = "Firacode" size = 10>
Oil
</font>

In [176]:
oil.columns = ['oil']
total_oil = pd.DataFrame(index=pd.date_range(start=train_sales.iloc[0,1],end=test_sales.iloc[-1,1],name="date"),columns=['oil'])
total_oil.update(oil)

In [177]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=oil.index,y=oil.oil,mode="lines"))
fig.show()

In [178]:
total_oil.reset_index(inplace=True)

In [179]:
total_oil.loc[0,'oil'] = 93.10

In [180]:
for i in total_oil.loc[total_oil.oil.isna()].index:
    j = i
    while (j < len(total_oil)) & (pd.isna(total_oil.loc[j+1,'oil'])):
        j += 1
    temp_arr = np.linspace(total_oil.loc[i-1,'oil'],total_oil.loc[j+1,'oil'],j-i+3)
    total_oil.loc[i:j,'oil'] = temp_arr[1:-1]

In [181]:
fig = make_subplots(rows=2,cols=1)
fig.add_trace(go.Scatter(x=oil.index,y=oil.oil,mode="lines"),row=1,col=1)
fig.add_trace(go.Scatter(x=total_oil['date'],y=total_oil.oil,mode="lines"),row=2,col=1)
fig.show()

In [182]:
train_sales.head()

id       date  store_nbr      family    sales  onpromotion
0   0 2013-01-01          1  AUTOMOTIVE 0.000000            0
1   1 2013-01-01          1   BABY CARE 0.000000            0
2   2 2013-01-01          1      BEAUTY 0.000000            0
3   3 2013-01-01          1   BEVERAGES 0.000000            0
4   4 2013-01-01          1       BOOKS 0.000000            0

In [183]:
total_train_oil = total_oil[total_oil.date.isin(train_sales.date)]
train_sales = train_sales.merge(total_train_oil,on='date',how='left')
train_sales.head()

id       date  store_nbr      family    sales  onpromotion       oil
0   0 2013-01-01          1  AUTOMOTIVE 0.000000            0 93.100000
1   1 2013-01-01          1   BABY CARE 0.000000            0 93.100000
2   2 2013-01-01          1      BEAUTY 0.000000            0 93.100000
3   3 2013-01-01          1   BEVERAGES 0.000000            0 93.100000
4   4 2013-01-01          1       BOOKS 0.000000            0 93.100000

#### Holidays
<font face = "Fira Code" size = 5>
<ol>
<li>Transferred column is the holiday that is transferred from its official date and the date it is trasnferred to is type == Transfer</li>
<li>Bridge are the days that are extended to the holidays/long weekend</li>
<li>Work day are the days that are made up(<i> of usually saturdays</i>) for the Bridged holidays</li>
<li>Additional days are the days which are given something like christmas eve</li>
</font>

In [184]:
type(holidays.iloc[0,0])

pandas._libs.tslibs.timestamps.Timestamp

In [185]:
holidays.head()

date     type    locale locale_name                    description  \
0 2012-03-02  Holiday     Local       Manta             Fundacion de Manta   
1 2012-04-01  Holiday  Regional    Cotopaxi  Provincializacion de Cotopaxi   
2 2012-04-12  Holiday     Local      Cuenca            Fundacion de Cuenca   
3 2012-04-14  Holiday     Local    Libertad      Cantonizacion de Libertad   
4 2012-04-21  Holiday     Local    Riobamba      Cantonizacion de Riobamba   

   transferred  
0        False  
1        False  
2        False  
3        False  
4        False

In [186]:
total = train_sales.copy()

In [187]:
total['holidays'] = np.NaN

In [188]:
display(total.head())
holidays.head()

id       date  store_nbr      family    sales  onpromotion       oil  \
0   0 2013-01-01          1  AUTOMOTIVE 0.000000            0 93.100000   
1   1 2013-01-01          1   BABY CARE 0.000000            0 93.100000   
2   2 2013-01-01          1      BEAUTY 0.000000            0 93.100000   
3   3 2013-01-01          1   BEVERAGES 0.000000            0 93.100000   
4   4 2013-01-01          1       BOOKS 0.000000            0 93.100000   

   holidays  
0       NaN  
1       NaN  
2       NaN  
3       NaN  
4       NaN

date     type    locale locale_name                    description  \
0 2012-03-02  Holiday     Local       Manta             Fundacion de Manta   
1 2012-04-01  Holiday  Regional    Cotopaxi  Provincializacion de Cotopaxi   
2 2012-04-12  Holiday     Local      Cuenca            Fundacion de Cuenca   
3 2012-04-14  Holiday     Local    Libertad      Cantonizacion de Libertad   
4 2012-04-21  Holiday     Local    Riobamba      Cantonizacion de Riobamba   

   transferred  
0        False  
1        False  
2        False  
3        False  
4        False

In [189]:
display(holidays.head(3))
display(total.head(3))
stores.head(3)

date     type    locale locale_name                    description  \
0 2012-03-02  Holiday     Local       Manta             Fundacion de Manta   
1 2012-04-01  Holiday  Regional    Cotopaxi  Provincializacion de Cotopaxi   
2 2012-04-12  Holiday     Local      Cuenca            Fundacion de Cuenca   

   transferred  
0        False  
1        False  
2        False

id       date  store_nbr      family    sales  onpromotion       oil  \
0   0 2013-01-01          1  AUTOMOTIVE 0.000000            0 93.100000   
1   1 2013-01-01          1   BABY CARE 0.000000            0 93.100000   
2   2 2013-01-01          1      BEAUTY 0.000000            0 93.100000   

   holidays  
0       NaN  
1       NaN  
2       NaN

store_nbr   city      state type  cluster
0          1  Quito  Pichincha    D       13
1          2  Quito  Pichincha    D       13
2          3  Quito  Pichincha    D        8

In [190]:
holidays.locale.unique()

array(['Local', 'Regional', 'National'], dtype=object)

In [191]:
holidays_without_transferred = holidays.query("transferred == False").index

In [192]:
for ind_num in holidays_without_transferred:
    date = holidays.loc[ind_num,'date']
    if holidays.loc[ind_num,'locale'] == 'National':
        total.loc[total['date'] == date,'holidays'] = 1
    elif holidays.loc[ind_num,'locale'] == 'Regional':
        reg_name = holidays.loc[ind_num,'locale_name']
        store_num = stores.loc[stores['state'] == reg_name,'store_nbr']
        total.loc[(total['date'] == date) & (total['store_nbr'].isin(store_num)),'holidays'] = 1
    else:
        city_name = holidays.loc[ind_num,'locale_name']
        store_num = stores.loc[stores['city'] == city_name,'store_nbr']
        total.loc[(total['date'] == date) & (total['store_nbr'].isin(store_num)),'holidays'] = 1


In [193]:
total.holidays.fillna(0,inplace=True)

In [194]:
holidays[holidays['date'] > '2013-01-01'].head()

date      type    locale locale_name  \
42 2013-01-05  Work Day  National     Ecuador   
43 2013-01-12  Work Day  National     Ecuador   
44 2013-02-11   Holiday  National     Ecuador   
45 2013-02-12   Holiday  National     Ecuador   
46 2013-03-02   Holiday     Local       Manta   

                           description  transferred  
42             Recupero puente Navidad        False  
43  Recupero puente primer dia del ano        False  
44                            Carnaval        False  
45                            Carnaval        False  
46                  Fundacion de Manta        False

In [195]:
total.head()

id       date  store_nbr      family    sales  onpromotion       oil  \
0   0 2013-01-01          1  AUTOMOTIVE 0.000000            0 93.100000   
1   1 2013-01-01          1   BABY CARE 0.000000            0 93.100000   
2   2 2013-01-01          1      BEAUTY 0.000000            0 93.100000   
3   3 2013-01-01          1   BEVERAGES 0.000000            0 93.100000   
4   4 2013-01-01          1       BOOKS 0.000000            0 93.100000   

   holidays  
0  1.000000  
1  1.000000  
2  1.000000  
3  1.000000  
4  1.000000

In [196]:
total['dayofweek']  = pd.DatetimeIndex(total['date']).dayofweek.to_numpy()

In [197]:
total['dayofweek'] = total['dayofweek'].apply(lambda x: 'Weekday' if x<5 else 'Weekend')

In [198]:
total = pd.concat([total,pd.get_dummies(total['dayofweek'])],axis=1).drop('dayofweek',axis=1)

In [199]:
total.head()

id       date  store_nbr      family    sales  onpromotion       oil  \
0   0 2013-01-01          1  AUTOMOTIVE 0.000000            0 93.100000   
1   1 2013-01-01          1   BABY CARE 0.000000            0 93.100000   
2   2 2013-01-01          1      BEAUTY 0.000000            0 93.100000   
3   3 2013-01-01          1   BEVERAGES 0.000000            0 93.100000   
4   4 2013-01-01          1       BOOKS 0.000000            0 93.100000   

   holidays  Weekday  Weekend  
0  1.000000        1        0  
1  1.000000        1        0  
2  1.000000        1        0  
3  1.000000        1        0  
4  1.000000        1        0

In [200]:
total['working_day'] = np.NaN
total.head()

id       date  store_nbr      family    sales  onpromotion       oil  \
0   0 2013-01-01          1  AUTOMOTIVE 0.000000            0 93.100000   
1   1 2013-01-01          1   BABY CARE 0.000000            0 93.100000   
2   2 2013-01-01          1      BEAUTY 0.000000            0 93.100000   
3   3 2013-01-01          1   BEVERAGES 0.000000            0 93.100000   
4   4 2013-01-01          1       BOOKS 0.000000            0 93.100000   

   holidays  Weekday  Weekend  working_day  
0  1.000000        1        0          NaN  
1  1.000000        1        0          NaN  
2  1.000000        1        0          NaN  
3  1.000000        1        0          NaN  
4  1.000000        1        0          NaN

In [201]:
total.loc[total.query("Weekday == 1 and holidays == 0").index,'working_day'] = 1
total['working_day'].fillna(0,inplace=True)
total.head()

id       date  store_nbr      family    sales  onpromotion       oil  \
0   0 2013-01-01          1  AUTOMOTIVE 0.000000            0 93.100000   
1   1 2013-01-01          1   BABY CARE 0.000000            0 93.100000   
2   2 2013-01-01          1      BEAUTY 0.000000            0 93.100000   
3   3 2013-01-01          1   BEVERAGES 0.000000            0 93.100000   
4   4 2013-01-01          1       BOOKS 0.000000            0 93.100000   

   holidays  Weekday  Weekend  working_day  
0  1.000000        1        0     0.000000  
1  1.000000        1        0     0.000000  
2  1.000000        1        0     0.000000  
3  1.000000        1        0     0.000000  
4  1.000000        1        0     0.000000

In [202]:
display(holidays.query("transferred == True").head())
working_dates = holidays.query("transferred == True").date

date     type    locale locale_name                 description  \
19  2012-10-09  Holiday  National     Ecuador  Independencia de Guayaquil   
72  2013-10-09  Holiday  National     Ecuador  Independencia de Guayaquil   
135 2014-10-09  Holiday  National     Ecuador  Independencia de Guayaquil   
255 2016-05-24  Holiday  National     Ecuador        Batalla de Pichincha   
266 2016-07-25  Holiday     Local   Guayaquil      Fundacion de Guayaquil   

     transferred  
19          True  
72          True  
135         True  
255         True  
266         True

In [203]:
total.loc[total['date'].isin(working_dates),'working_day'] = 1

In [204]:
oil = pd.read_csv('./store-sales-time-series-forecasting/oil.csv')

In [205]:
train_sales.iloc[0,1]

Timestamp('2013-01-01 00:00:00')

In [206]:
test_sales.head()

id       date  store_nbr      family  onpromotion
0  3000888 2017-08-16          1  AUTOMOTIVE            0
1  3000889 2017-08-16          1   BABY CARE            0
2  3000890 2017-08-16          1      BEAUTY            2
3  3000891 2017-08-16          1   BEVERAGES           20
4  3000892 2017-08-16          1       BOOKS            0

In [207]:
oil[oil['date'] == '2017-08-17']

date  dcoilwtico
1207  2017-08-17   47.070000

### Total Preprocess

In [208]:
def preprocess(data:pd.DataFrame,oil:pd.DataFrame,train_sales:pd.DataFrame,test_sales:pd.DataFrame,holidays:pd.DataFrame):

    def preprocess_oil(dframed:pd.DataFrame):
        dframe = dframed.copy()
        dframe['date'] = pd.to_datetime(dframe['date'])
        dframe.set_index('date',inplace=True)
        dframe.columns = ['oil']
        total_oil = pd.DataFrame(index=pd.date_range(start=train_sales.iloc[0,1],end=test_sales.iloc[-1,1],name="date"),columns=['oil'],dtype=np.float32)
        total_oil.update(dframe)
        total_oil.reset_index(inplace=True)
        total_oil.loc[0,'oil'] = 93.10
        for i in total_oil.loc[total_oil.oil.isna()].index:
            j = i
            while (j < len(total_oil)) & (pd.isna(total_oil.loc[j+1,'oil'])):
                j += 1
            temp_arr = np.linspace(total_oil.loc[i-1,'oil'],total_oil.loc[j+1,'oil'],j-i+3,dtype=np.float32)
            total_oil.loc[i:j,'oil'] = temp_arr[1:-1]
        return total_oil

    df = data.copy()
    total_oil = preprocess_oil(oil)
    temp_oil = total_oil[total_oil.date.isin(df.date)]
    df = df.merge(temp_oil,on='date',how='left')
    for ind_num in holidays_without_transferred:
        date = holidays.loc[ind_num,'date']
        if holidays.loc[ind_num,'locale'] == 'National':
            df.loc[df['date'] == date,'holidays'] = 1
        elif holidays.loc[ind_num,'locale'] == 'Regional':
            reg_name = holidays.loc[ind_num,'locale_name']
            store_num = stores.loc[stores['state'] == reg_name,'store_nbr']
            df.loc[(df['date'] == date) & (df['store_nbr'].isin(store_num)),'holidays'] = 1
        else:   
            city_name = holidays.loc[ind_num,'locale_name']
            store_num = stores.loc[stores['city'] == city_name,'store_nbr']
            df.loc[(df['date'] == date) & (df['store_nbr'].isin(store_num)),'holidays'] = 1

    df.holidays.fillna(0,inplace=True)
    df['dayofweek']  = pd.DatetimeIndex(df['date']).dayofweek.to_numpy()
    df['dayofweek'] = df['dayofweek'].apply(lambda x: 'Weekday' if x<5 else 'Weekend')
    df = pd.concat([df,pd.get_dummies(df['dayofweek'])],axis=1).drop('dayofweek',axis=1)
    df['working_day'] = np.NaN
    df.loc[df.query("Weekday == 1 and holidays == 0").index,'working_day'] = 1
    df['working_day'].fillna(0,inplace=True)
    df.loc[total['date'].isin(working_dates),'working_day'] = 1
    return df

In [209]:
train_sales = pd.read_csv('./store-sales-time-series-forecasting/train.csv')
train_sales['date'] = pd.to_datetime(train_sales['date'])
train_sales.head()

id       date  store_nbr      family    sales  onpromotion
0   0 2013-01-01          1  AUTOMOTIVE 0.000000            0
1   1 2013-01-01          1   BABY CARE 0.000000            0
2   2 2013-01-01          1      BEAUTY 0.000000            0
3   3 2013-01-01          1   BEVERAGES 0.000000            0
4   4 2013-01-01          1       BOOKS 0.000000            0

In [210]:
new_total = preprocess(train_sales,oil=oil,train_sales=train_sales,test_sales=test_sales,holidays=holidays)

In [211]:
total.head()

id       date  store_nbr      family    sales  onpromotion       oil  \
0   0 2013-01-01          1  AUTOMOTIVE 0.000000            0 93.100000   
1   1 2013-01-01          1   BABY CARE 0.000000            0 93.100000   
2   2 2013-01-01          1      BEAUTY 0.000000            0 93.100000   
3   3 2013-01-01          1   BEVERAGES 0.000000            0 93.100000   
4   4 2013-01-01          1       BOOKS 0.000000            0 93.100000   

   holidays  Weekday  Weekend  working_day  
0  1.000000        1        0     0.000000  
1  1.000000        1        0     0.000000  
2  1.000000        1        0     0.000000  
3  1.000000        1        0     0.000000  
4  1.000000        1        0     0.000000

In [212]:
total['oil'] = total['oil'].astype(np.float32)

In [213]:
transformed_total = total.groupby(['store_nbr','family','date']).sum()

In [214]:
transformed_total.head()

id    sales  onpromotion       oil  \
store_nbr family     date                                               
1         AUTOMOTIVE 2013-01-01     0 0.000000            0 93.099998   
                     2013-01-02  1782 2.000000            0 93.139999   
                     2013-01-03  3564 3.000000            0 92.970001   
                     2013-01-04  5346 3.000000            0 93.120003   
                     2013-01-05  7128 5.000000            0 93.146667   

                                 holidays  Weekday  Weekend  working_day  
store_nbr family     date                                                 
1         AUTOMOTIVE 2013-01-01  1.000000        1        0     0.000000  
                     2013-01-02  0.000000        1        0     1.000000  
                     2013-01-03  0.000000        1        0     1.000000  
                     2013-01-04  0.000000        1        0     1.000000  
                     2013-01-05  1.000000        0        1     0.000000

In [218]:
X = transformed_total[['sales','onpromotion','oil','holidays','Weekday','Weekend','working_day']].to_numpy()
ids = transformed_total['id']

In [226]:
X = X.reshape(-1,time_steps,7)

In [228]:
total_oil.shape

(1704, 2)